In [1]:
from market_growth_analysis.etl.web_scraping import scrape_company_data, process_sector, process_prices_company, get_sector_data, get_industry_data, parser, get_price_info

import concurrent
import tqdm

from bs4 import BeautifulSoup
import requests

import yfinance as yf
import pandas as pd
import os
from os.path import join
from datetime import datetime
from pathlib import Path 

# Extract Prices

In [2]:
path = '../../data/intermediate_02/financial-sheets.csv'
financial_sheet = pd.read_csv(path)
companys = pd.read_csv(path).sort_values(by='ticker')['ticker'].dropna().unique()

In [3]:
import concurrent.futures
from tqdm import tqdm
import logging

# Create a ThreadPoolExecutor
executor = concurrent.futures.ThreadPoolExecutor()

# List to store the future objects
futures = []

prices = pd.DataFrame()

# Iterate over the companies and submit the tasks to the executor
for company in companys:
    future = executor.submit(process_prices_company, company, financial_sheet)
    futures.append(future)

# Use tqdm to track the progress of the loop
results = []
with tqdm(total=len(companys)) as pbar:
    for future in concurrent.futures.as_completed(futures):
        result = future.result()
        if result is not None:
            results.append(result)
        pbar.update(1)

# Combine the results
prices = pd.concat(results, ignore_index=True)


  0%|          | 0/5554 [00:00<?, ?it/s]c:\Users\germa\AppData\Local\Programs\Python\Python39\lib\site-packages\market_growth_analysis\etl\web_scraping.py:182: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ticker_file['YearMonth'] = ticker_file['Date'].str.slice(0, 7)
c:\Users\germa\AppData\Local\Programs\Python\Python39\lib\site-packages\market_growth_analysis\etl\web_scraping.py:189: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  filtered_hist['Date'] = pd.to_datetime(filtered_hist['Date'])
c:\Users\germa\

In [4]:
prices[prices['ticker'] == 'ITRN']

longevity       High        Low       Open      Close     Volume  \
40122          0  17.129999  14.200000  14.390000  15.950000  2252900.0   
40123          1  16.730000  14.560000  15.960000  15.050000   912300.0   
40124          2  11.200000   9.950000  10.290000  11.070000   859900.0   
40125          3   8.940000   7.150000   7.720000   7.310000  1223100.0   
40126          4  13.680000  12.670000  12.960000  12.820000   291100.0   
40127          5  17.799999  15.520000  15.890000  17.490000   376800.0   
40128          6  14.000000  12.220000  12.680000  13.660000   189600.0   
40129          7  13.580000  12.750000  13.080000  13.570000   382700.0   
40130          8  21.879999  19.520000  19.920000  21.639999   619500.0   
40131          9  23.490000  21.180000  21.629999  22.040001   369400.0   
40132         10  20.600000  17.760000  20.170000  18.930000   310200.0   
40133         11  26.799999  24.570000  25.000000  26.500000   477700.0   
40134         12  35.779999  33.400002  35.599998  34.200001   788300.0   
40135         13  35.169998  29.379999  33.290001  32.060001   688900.0   
40136         14  25.450001  21.530001  23.850000  25.129999  1736700.0   
40137         15  19.469999  17.260000  18.410000  19.049999  1222500.0   
40138         16  26.969999  23.920000  26.090000  26.670000  1217600.0   
40139         17  23.639999  20.830000  23.559999  21.129999   922700.0   

        Adjclose       Date  year ticker  Growth -1  Growth +1  Growth +5  \
40122  -0.194557 2005-12-01  2005   ITRN        NaN  -0.056426   0.096552   
40123  -0.185464 2006-12-01  2006   ITRN  -0.056426  -0.264452  -0.092359   
40124  -0.147178 2007-12-01  2007   ITRN  -0.264452  -0.339657   0.225836   
40125  -0.205045 2008-12-01  2008   ITRN  -0.339657   0.753762   1.960328   
40126  -0.406597 2009-12-01  2009   ITRN   0.753762   0.364275   0.719189   
40127  -0.608775 2010-12-01  2010   ITRN   0.364275  -0.218982   0.082333   
40128  -0.506338 2011-12-01  2011   ITRN  -0.218982  -0.006589   0.939971   
40129  -0.641379 2012-12-01  2012   ITRN  -0.006589   0.594694   1.520265   
40130  -1.205572 2013-12-01  2013   ITRN   0.594694   0.018484   0.481516   
40131  17.698345 2014-12-01  2014   ITRN   0.018484  -0.141107   0.140200   
40132  15.786793 2015-12-01  2015   ITRN  -0.141107   0.399894   0.006339   
40133  22.998617 2016-12-01  2016   ITRN   0.399894   0.290566   0.006415   
40134  30.780344 2017-12-01  2017   ITRN   0.290566  -0.062573  -0.382164   
40135  29.701473 2018-12-01  2018   ITRN  -0.062573  -0.216157        NaN   
40136  23.844652 2019-12-01  2019   ITRN  -0.216157  -0.241942        NaN   
40137  18.554525 2020-12-01  2020   ITRN  -0.241942   0.400000        NaN   
40138  26.670000 2021-12-01  2021   ITRN   0.400000  -0.207724        NaN   
40139  21.129999 2022-12-01  2022   ITRN  -0.207724        NaN        NaN   

       Growth -10  Growth -5  
40122         NaN        NaN  
40123         NaN        NaN  
40124         NaN        NaN  
40125         NaN        NaN  
40126         NaN        NaN  
40127    0.096552        NaN  
40128   -0.092359        NaN  
40129    0.225836        NaN  
40130    1.960328        NaN  
40131    0.719189        NaN  
40132    0.082333   0.186834  
40133    0.939971   0.760797  
40134    1.520265   2.089431  
40135    0.481516   3.385773  
40136    0.140200   0.960218  
40137    0.006339   0.089194  
40138    0.006415   0.952416  
40139   -0.382164   0.557111

In [5]:
# Export the dataframe
filepath = Path(f'../../data/raw_01/prices.csv')  
filepath.parent.mkdir(parents=True, exist_ok=True)  
prices.to_csv(filepath)